In [ ]:
import os

os.environ["GES_TABLE_DIR"] = "/data/cvl_exj3/TABLES/DSC"

In [ ]:
from pprint import pprint

import yaml
from cartopy import crs as ccrs
from casys.elements import CyclePassFmt

from casys import (
    AxeParams,
    CasysPlot,
    CyclePassFormatter,
    DataParams,
    DateHandler,
    Field,
    GridParams,
    NadirData,
    PlotParams,
    PlotTemplate,
    Position,
    TextParams,
)

NadirData.enable_loginfo()

In [ ]:
start = DateHandler.from_orf("C_J3_GDRD", 122, 1, pos="first")
end = DateHandler.from_orf("C_J3_GDRD", 122, 154, pos="last")

In [ ]:
ad = NadirData(
    date_start=start,
    date_end=end,
    source="TABLE_C_J3_B_GDRD",
    orf="C_J3_GDRD",
    time="time",
    longitude="LONGITUDE",
    latitude="LATITUDE",
)

var_sig0 = ad.fields["SIGMA0.ALTI"]
var_sla = Field(
    name="SLA",
    source="ORBIT.ALTI - RANGE.ALTI - MEAN_SEA_SURFACE.MODEL.CNESCLS15",
    unit="m",
)
var_wind = Field(
    name="wind", source="IIF(FLAG_VAL.ALTI==0, WIND_SPEED.ALTI,DV)", unit="m/s"
)
ad.add_raw_data(name="Sigma 0", field=var_sig0)
ad.add_raw_data(name="Wind speed", field=var_wind)

ad.add_time_stat(
    name="Sigma 0 by day", freq="day", field=var_sig0, stats=["mean", "std", "var"]
)
ad.add_time_stat(
    name="SIG0 pass", freq="pass", field=var_sig0, stats=["mean", "std", "var"]
)
ad.add_time_stat(
    name="SLA pass", freq="pass", field=var_sla, stats=["mean", "std", "var"]
)

ad.compute()

# How to use plot templates

PlotTemplate is an object allowing to specify properties for each element of a plot [[doc](../cp_templates.rst)].

## Create a simple plot template

In [ ]:
t = PlotTemplate(
    title=AxeParams(label={"size": "xx-large", "weight": "bold"}),
    stat_bar=AxeParams(
        label={"fontsize": "large"},
        position="top",
        enabled=True,
    ),
)

### Create a plot with this template, and set other params

In [ ]:
pparams = PlotParams(grid=True)

tparams = TextParams(title={"weight": "light", "color": "red"})

plot = CasysPlot(
    data=ad,
    data_name="Sigma 0 by day",
    stat="mean",
    template=t,
    plot_params=pparams,
    text_params=tparams,
)
plot.set_ticks(fmt="CP")
plot.show()

### Get plot template

In [ ]:
t = plot.template

### Store plot template

In [ ]:
t.store(name="simple_t", path="templates.yaml", overwrite=True)

### Load the template

In [ ]:
tt = PlotTemplate.load(name="simple_t", path="templates.yaml")

### Create another plot with this template

In [ ]:
plot = CasysPlot(data=ad, data_name="SLA pass", stat="mean", template=tt)
plot.show()

## Create a template with altimetric ticks

In [ ]:
template = PlotTemplate(
    legend=AxeParams(label={"size": "large"}),
    title=AxeParams(label={"size": "x-large", "weight": "bold"}),
    plot=PlotParams(grid=True),
    stat_bar=AxeParams(
        label={"fontsize": "large"},
        position="top",
        enabled=True,
    ),
    x1=AxeParams(
        label={"label": "cycle"},
        values=CyclePassFormatter(orf=ad.orf, fmt=CyclePassFmt.C),
        enabled=True,
    ),
)

In [ ]:
plot = CasysPlot(data=ad, data_name="Sigma 0 by day", stat="mean", template=template)
plot.show()

In [ ]:
t = plot.template

In [ ]:
plot = CasysPlot(data=ad, data_name="SLA pass", stat="mean", template=t)
plot.show()

## Create a carto plot and reuse its template

In [ ]:
pparams = PlotParams(
    fill_ocean=False,
    projection=ccrs.PlateCarree(central_longitude=180.0),
    grid=True,
    color_limits=(10, 17),
    x_limits=(40, 180),
    y_limits=(-90, 90),
)
tparams = TextParams(
    legend={
        "size": "large",
    },
    title={"size": "x-large", "weight": "bold"},
)
color_bar_param = AxeParams(
    label={"label": "m"}, ticks={"labelsize": "medium"}, enabled=True
)

plot = CasysPlot(
    data=ad,
    data_name="Sigma 0",
    plot="map",
    plot_params=pparams,
    text_params=tparams,
)

plot.add_color_bar(position="right", params=color_bar_param)
plot.add_hist_bar(position="bottom")
plot.set_title("Custom title")

plot.show()

In [ ]:
t = plot.template

In [ ]:
t.store(name="slabox_t", path="templates.yaml")

In [ ]:
tt = PlotTemplate.load(name="slabox_t", path="templates.yaml")
plot = CasysPlot(data=ad, data_name="Wind speed", plot="map", template=tt)
plot.show()

## Create graph template

In [ ]:
t = PlotTemplate(
    plot=PlotParams(
        fill_ocean=False,
        projection=ccrs.PlateCarree(central_longitude=180.0),
        grid=True,
        color_limits=(10, 17),
        y_limits=(-90, 90),
        fig_height=4.5,
    ),
    title=AxeParams(label={"label": "A Title", "fontsize": "x-large"}, enabled=True),
    x1=AxeParams(
        label={"label": "default_x1_label", "fontsize": "medium"}, enabled=True
    ),
    x2=AxeParams(
        label={"label": "default_x2_label", "fontsize": "medium"}, enabled=True
    ),
    y1=AxeParams(
        label={"label": "default_y1_label", "fontsize": "medium"}, enabled=True
    ),
    y2=AxeParams(
        label={"label": "default_y2_label", "fontsize": "medium"}, enabled=True
    ),
    stat_bar=AxeParams(
        label={"fontsize": "small", "weight": "light"},
        position="top",
        enabled=True,
    ),
    text=TextParams(
        legend={
            "size": "large",
        },
        title={"label": "Other title", "weight": "bold"},
    ),
    ticks_spaces=[(Position.TOP, 0.1), (Position.BOTTOM, 0.1)],
)

In [ ]:
plot = CasysPlot(data=ad, data_name="Sigma 0", template=t)
plot.show()

### Get the template and enrich it with set_template

In [ ]:
t = plot.template

t2 = PlotTemplate.set_template(
    template=t,
    data_params=DataParams(
        x_limits=(
            DateHandler("2019/06/04T07:00:00"),
            DateHandler("2019/06/04T10:00:00"),
        )
    ),
)
plot = CasysPlot(data=ad, data_name="Sigma 0", template=t2)
plot.show()

## Create map template

In [ ]:
t = PlotTemplate(
    plot=PlotParams(
        fill_ocean=False,
        projection=ccrs.PlateCarree(central_longitude=180.0),
        grid=False,
        color_limits=(10, 17),
        y_limits=(-90, 90),
        fig_height=4.5,
    ),
    color_bar=AxeParams(position="right", enabled=True),
    stat_bar=AxeParams(
        label={"fontsize": "small", "weight": "light"},
        position="top",
        enabled=True,
    ),
    text=TextParams(
        legend={
            "size": "large",
        },
        title={"label": "title", "size": "x-large", "weight": "bold"},
    ),
    grid=GridParams(
        line_properties={"linestyle": "dashed"}, right_labels=False, enabled=True
    ),
    ticks_spaces=[(Position.TOP, 0.1), (Position.BOTTOM, 0.1)],
)

In [ ]:
plot = CasysPlot(data=ad, data_name="Wind speed", plot="map", template=t)

plot.show()

### Get the template and enrich it with set_template

In [ ]:
t = plot.template

t2 = PlotTemplate.set_template(template=t, plot_params=PlotParams(color_map="autumn"))

In [ ]:
plot = CasysPlot(
    data=ad,
    data_name="Wind speed",
    plot="map",
    template=t2,
)

plot.show()

## Merged plots

In [ ]:
tparams = TextParams(
    legend={"size": "large"},
    title={"size": "x-large", "weight": "bold"},
)

pparams = PlotParams(grid=True)

stat_bar_param = AxeParams(
    label={
        "fontsize": "large",
    }
)

In [ ]:
plot = CasysPlot(
    data=ad, data_name="SLA pass", stat="mean", plot_params=pparams, text_params=tparams
)
plot.set_legend("Sla")
plot.add_stat_bar(params=stat_bar_param)
plot.set_ticks(position="top", fmt="P")

plot2 = CasysPlot(data=ad, data_name="SIG0 pass", stat="mean")
plot2.set_legend("Sig0")
plot2.add_stat_bar(params=stat_bar_param)
plot.add_plot(plot2)

plot.set_text_size(elements=["axes_ticks"], size="large")

plot.set_title("Sentinel-6 SWH")
plot.set_ticks(fmt="CP")
plot.show()

In [ ]:
t = plot.template

t.store(name="merged_t", path="templates.yaml")

In [ ]:
plot = CasysPlot(data=ad, data_name="SLA pass", stat="mean", template=t)

t2 = plot2.template
plot2 = CasysPlot(data=ad, data_name="SIG0 pass", stat="mean", template=t2)

plot.add_plot(plot2)
plot.show()

## Show yaml file content

In [ ]:
with open(r"templates.yaml") as file:
    templates = yaml.load(file, Loader=yaml.FullLoader)
    pprint(templates)

In [ ]:
os.remove("templates.yaml")